In [ ]:
#Divide and Conquer algorithm
from typing import List
array = [1,2,1,1,2,2,1,1]
s = 4

from pyspark import SparkContext
rdd = sc.parallelize(array,2).cache()

def sequential(nums:List[int]):
    length = len(nums)
    count = 0
    left,right,tmps = 0,0,0
    
    while right<length:
        while right<length and tmps <= s:
            if tmps == s:
                count+=1
            tmps+=nums[right]
            right+=1
        while tmps>s:
            tmps-=nums[left]
            left+=1
    #(tmps == s)check whether the last window after moving left can sum up to s
    return count+(tmps == s)

def divide(it):
    def leftSubArray(array):
        #return the longest interval starting with begining index
        #whose sum is less than S
        for i in range(len(array)):
            if sum(array[0:i+1])>=s:
                return array[0:i]
    def rightSubArray(array):
        #return the longest interval starting with begining index
        #whose sum is less than S
        for i in range(len(array),-1,-1):
            if sum(array[i:])>=s:
                return array[i+1:]
            
    array = list(it)
    yield [sequential(array), leftSubArray(array), rightSubArray(array)]
    
def conquer(X):
    total=0
    prevright = []
    for partres in X:
        #partres is the partition result
        (subcount, subleft, subright) = partres
        total+=subcount
        total +=sequential(prevright+subleft)
        prevright = subright
    return total

X = rdd.mapPartitions(divide).collect()
result = conquer(X)
print(result)
        
    
    

In [60]:
!pip install graphframes

In [61]:
from graphframes import *
from pyspark.sql.functions import *

In [62]:
# Vertics DataFrame
v = spark.createDataFrame([
  ("a", "Alice", 34),
  ("b", "Bob", 36),
  ("c", "Charlie", 37),
  ("d", "David", 29),
  ("e", "Esther", 32),
  ("f", "Fanny", 38),
  ("g", "Gabby", 60)
], ["id", "name", "age"])

# Edges DataFrame(directed edges)
e = spark.createDataFrame([
  ("a", "b", "friend"),
  ("b", "c", "follow"),
  ("c", "b", "follow"),
  ("f", "c", "follow"),
  ("e", "f", "follow"),
  ("e", "d", "friend"),
  ("d", "a", "friend"),
  ("a", "e", "friend"),
  ("g", "e", "follow")
], ["src", "dst", "relationship"])

# Create a GraphFrame
g = GraphFrame(v, e)

g.vertices.show()
g.edges.show()

/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/sql/dataframe.py:148: UserWarning: DataFrame.sql_ctx is an internal property, and will be removed in future releases. Use DataFrame.sparkSession instead.
  warnings.warn(


+---+-------+---+
| id|   name|age|
+---+-------+---+
|  a|  Alice| 34|
|  b|    Bob| 36|
|  c|Charlie| 37|
|  d|  David| 29|
|  e| Esther| 32|
|  f|  Fanny| 38|
|  g|  Gabby| 60|
+---+-------+---+

+---+---+------------+
|src|dst|relationship|
+---+---+------------+
|  a|  b|      friend|
|  b|  c|      follow|
|  c|  b|      follow|
|  f|  c|      follow|
|  e|  f|      follow|
|  e|  d|      friend|
|  d|  a|      friend|
|  a|  e|      friend|
|  g|  e|      follow|
+---+---+------------+



In [64]:
g.find('!()-[]->(a)').show()

/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/sql/dataframe.py:127: UserWarning: DataFrame constructor is internal. Do not directly use it.
  warnings.warn("DataFrame constructor is internal. Do not directly use it.")


+--------------+
|             a|
+--------------+
|{g, Gabby, 60}|
+--------------+



In [72]:
# spark graph
indegree = e.filter('relationship="follow"').groupBy('dst').count()\
            .select('dst','count').withColumnRenamed('count','indegree')
#rename count as indegree
outdegree = e.filter('relationship="follow"').groupBy('src').count()\
            .select('src','count').withColumnRenamed('count','outdegree')
avgoutdegree = outdegree.agg(avg('outdegree')).take(1)[0][0]#[0][0] get the value
avgoutdegree
outdegree = outdegree.filter(outdegree.outdegree>avgoutdegree)
result = indegree.join(outdegree, indegree.dst == outdegree.src).filter('indegree>outdegree')
result.show()

+---+--------+---+---------+
|dst|indegree|src|outdegree|
+---+--------+---+---------+
+---+--------+---+---------+



In [ ]:
# spark graph
indegree = e.filter('relationship="follow"').groupBy('dst').count()\
            .select('dst','count').withColumnRenamed('count','indegree')
#rename count as indegree
outdegree = e.filter('relationship="follow"').groupBy('src').count()\
            .select('src','count').withColumnRenamed('count','outdegree')
avgoutdegree = outdegree.groupBy().avg('outdegree').take(1)[0][0]

outdegree = outdegree.filter(outdegree.outdegree>avgoutdegree)
result = indegree.join(outdegree,indegree.dst == outdegree.src)\
            .filter('indegree>outdegree')\
            .join(v,v.id == e.dst).select(v.name).show()
#should join with vertex set







In [ ]:
#graph motif
result = g.find('(a)-[e1]->(b);(b)-[e2]->(c);(c)-[e3]->(a)')\
        .filter('e1.relationship="friend"').filter('e2.relationship="friend"')\
        .filter('e3.relationship="friend"').filter('a.id<b.id')\
        .filter('a.id<c.id').select('a.name','b.name','c.name')\
        .show()


In [ ]:
# Find triangles
triangles = g.find("(a)-[]->(b); (b)-[]->(c); (c)-[]->(a)")#two joins finding a triangles a->b->c(src)
triangles = triangles.filter("a.id < b.id AND a.id < c.id")#
triangles.show()

In [ ]:
from pyspark.streaming import StreamingContext

# Stateful word count

ssc = StreamingContext(sc, 5)
# Provide a checkpointing directory.  Required for stateful transformations(restore state from previous time)
ssc.checkpoint("checkpoint")

#rdd = sc.textFile('adj_noun_pairs.txt', 8)
rdd = sc.textFile('adj_noun_pairs.txt', 8).map(lambda l:tuple(l.split())).filter(lambda p:len(p)==2)

rddQueue = rdd.randomSplit([1]*10, 123)#10 batches, each batch is smaller
lines = ssc.queueStream(rddQueue)

#newValues a list of size 1 for word count; runningCount is current count
#if key doesn't exist in the state
def updateFunc(newValues, runningCount):
    if runningCount is None:
        runningCount = 0
    return sum(newValues, runningCount)#add new count to the running count; 
    #sum(list, addition value added to the final sum)
    # add the new values with the previous running count to get the new count

#other rdd(after every batch, therer is a new state)(how the state is updated after each batch, initial is empty)
running_counts = lines.map(lambda word: (word, 1))\
                      .updateStateByKey(updateFunc)#same keys are grouped together

counts_sorted = running_counts.transform(lambda rdd: rdd.sortBy(lambda x: x[1], False))

def printResults(rdd):
    #print("Total distinct words: ", rdd.count())
    print(rdd.take(10))


counts_sorted.foreachRDD(printResults)

ssc.start()
ssc.awaitTermination(50)
ssc.stop(False)
print("Finished")

In [ ]:
from pyspark.sql.functions import *

def parse_line(l):
    x = l.split("\t")
    return (x[0], float(x[1]))

word_sentiments = spark.createDataFrame(sc.textFile("../data/AFINN-111.txt") 
                    .map(parse_line), ['word', 'sentiment']).cache()

lines = spark\
        .readStream\
        .format('socket')\
        .option('host', 'localhost')\
        .option('port', '9999')\
        .option('includeTimestamp', 'true')\
        .load()

# Split the lines into words and explode the array
words = lines.select(explode(split(lines.value, ' ')).alias('word'), lines.timestamp)

happy_words = words.groupBy(window(words.timestamp,"10 seconds", "5 seconds"),
                           words.word)\
                           .count()\
                           .join(word_sentiments, words.word == word_sentiments.word)\
                           .select(col("window"), words.word, col("count"),col("sentiment"))\
                           .withColumn('sentiment', col("count")*col("sentiment"))\
                           .orderBy(col("sentiment").desc())

# Output the results in complete mode
query = happy_words.writeStream\
                    .outputMode('complete')\
                    .format('console')\
                    .option('truncate','false')\
                    .trigger(processingTime='5 seconds')\
                    .start()

query.awaitTermination(25)
query.stop()
print("Finished")

In [ ]:
from pyspark.streaming import StreamingContext

# Stateful word count

ssc = StreamingContext(sc, 5)
# Provide a checkpointing directory.  Required for stateful transformations(restore state from previous time)
ssc.checkpoint("checkpoint")

#rdd = sc.textFile('adj_noun_pairs.txt', 8)
rdd = sc.textFile('adj_noun_pairs.txt', 8).map(lambda l:tuple(l.split())).filter(lambda p:len(p)==2)

rddQueue = rdd.randomSplit([1]*10, 123)#10 batches, each batch is smaller
lines = ssc.queueStream(rddQueue)

#newValues a list of size 1 for word count; runningCount is current count
#if key doesn't exist in the state
def updateFunc(newValues, runningCount):
    if runningCount is None:
        runningCount = 0
    return sum(newValues, runningCount)#add new count to the running count; 
    #sum(list, addition value added to the final sum)
    # add the new values with the previous running count to get the new count

#other rdd(after every batch, therer is a new state)(how the state is updated after each batch, initial is empty)
running_counts = lines.map(lambda word: (word, 1))\
                      .updateStateByKey(updateFunc)#same keys are grouped together

#x[0][1] represent noun
#same noun, return the one with the larger frequency
#map orginal tupe([adj,noun],count)
counts_sorted = running_counts.map(lambda x:(x[0][1],x)).reduceByKey(lambda x,y: x if x[1]>y[1] else y)\
                .map(lambda x: x[1]).transform(lambda rdd: rdd.sortBy(lambda x: x[1], False))

def printResults(rdd):
    #print("Total distinct words: ", rdd.count())
    print(rdd.take(10))


counts_sorted.foreachRDD(printResults)

ssc.start()
ssc.awaitTermination(50)
ssc.stop(False)
print("Finished")

In [ ]:
#sql
from pyspark.sql.functions import *
select_condition = 'Brand = \'' + RequiredBrand + '\' and Container = \'' + RequiredContainer + '\''
dfProductSelect = dfProduct.where(select_condition).select("Product_ID")
dfJoin = dfProductSelect.join(dfTransaction, 'Product_ID')
dfAvg = dfJoin.groupBy("Product_ID").avg("SaleQuantity").withColumnRenamed("avg(SaleQuantity)", "avgQuantity")
dfFinal = dfAvg.join(dfJoin, 'Product_ID').filter("avgQuantity > SaleQuantity")
dfFinal.select('*',(dfFinal.SalePrice*dfFinal.SaleQuantity).alias('revenue')).select(sum(col('revenue'))).show()

In [3]:
odd = sc.accumulator (0)
even = 0
def count(element ):
    global even
    if element % 2 == 0:
        even += 1
    else:
        odd.add (1)
sc.parallelize ([1, 6, 7, 8, 3, 4, 4, 2]). foreach(count)
print(odd ,even)

3 0


In [8]:
A = sc.parallelize(range(1, 1000))
t = 100
B = A.filter(lambda x: x*x < t)
t = 200
C = B.filter(lambda x: x*x < t)
print(C.count())

14


In [9]:
e=sc.parallelize ([(1 ,2) ,(1 ,3) ,(1 ,4) ,(2 ,1) ,(3 ,1) ,(4 ,1)]).toDF(["src","dst"])
r = sc.parallelize ([(1 ,) ,(2 ,) ,(3 ,) ,(4 ,)]). toDF(['src'])
r1 = e.join(r, 'src'). groupBy('dst'). count ()
r1.show()

+---+-----+
|dst|count|
+---+-----+
|  1|    3|
|  3|    1|
|  2|    1|
|  4|    1|
+---+-----+



In [58]:
import time
from operator import add
data = sc.parallelize(range(0,9)).filter(lambda x: x<=int(time.time())%10)
print(data.map(lambda x: x+1).reduce(add)+ data.map(lambda x: x-1).reduce(add))
print(data.reduce(add)*2)

72
72
23/05/18 16:27:10 WARN HeartbeatReceiver: Removing executor driver with no recent heartbeats: 446176 ms exceeds timeout 120000 ms
23/05/18 16:27:10 WARN SparkContext: Killing executors is not supported by current scheduler.


In [4]:
from pyspark.streaming import StreamingContext 
ssc = StreamingContext(sc, 2) 

numPartitions = 8 
sailors = sc.textFile('sailors.txt', numPartitions).map(lambda l: tuple(l.split(','))) 
boats = sc.textFile('boats.txt', numPartitions).map(lambda l: tuple(l.split(','))) 
rdd = sc.textFile('reserves.txt', numPartitions) 
rddQueue = rdd.randomSplit([1]*3, 123) 
lines = ssc.queueStream(rddQueue) 
reserves = lines.map(lambda l: tuple(l.split(',')))

# FILL IN YOUR CODE HERE
# Filter the boats to only keep the red ones
redBoats = boats.filter(lambda x: x[1] == "red").map(lambda x:x[0])
# Join the reserves with the red boats to only keep the reserves for red boats
#reserves = reserves.transform(lambda rdd: rdd.join(redBoats.map(lambda x: (x[0], None))).map(lambda x: x[1][0]))
new = reserves.transform(lambda rdd: rdd.filter(lambda x: x in redBoats.collect()))


# Print the sailor names for each batch
new.pprint()

ssc.start() 
ssc.awaitTermination(20) 
ssc.stop(False) 



Py4JJavaError: An error occurred while calling o1094.start.
: java.lang.IllegalStateException: Only one StreamingContext may be started in this JVM. Currently running StreamingContext was started atorg.apache.spark.streaming.api.java.JavaStreamingContext.start(JavaStreamingContext.scala:557)
java.base/jdk.internal.reflect.DirectMethodHandleAccessor.invoke(DirectMethodHandleAccessor.java:104)
java.base/java.lang.reflect.Method.invoke(Method.java:577)
py4j.reflection.MethodInvoker.invoke(MethodInvoker.java:244)
py4j.reflection.ReflectionEngine.invoke(ReflectionEngine.java:357)
py4j.Gateway.invoke(Gateway.java:282)
py4j.commands.AbstractCommand.invokeMethod(AbstractCommand.java:132)
py4j.commands.CallCommand.execute(CallCommand.java:79)
py4j.ClientServerConnection.waitForCommands(ClientServerConnection.java:182)
py4j.ClientServerConnection.run(ClientServerConnection.java:106)
java.base/java.lang.Thread.run(Thread.java:833)
	at org.apache.spark.streaming.StreamingContext$.org$apache$spark$

Traceback (most recent call last):
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/serializers.py", line 458, in dumps
    return cloudpickle.dumps(obj, pickle_protocol)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 73, in dumps
    cp.dump(obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/rdd.py", line 356, in __getnewargs__
    raise RuntimeError(
RuntimeError: It appears that you are attempting to broadcast an RDD or reference an RDD from an action or transformation. RDD transformations and actions can only be invoked by the driver, not inside of other transformations; for example, rdd1.map(lambda x: rdd2.values.count() * x) is invalid because the values transformation and count action cannot be performed inside of t

23/05/18 21:41:22 ERROR JobScheduler: Error generating jobs for time 1684417282000 ms
org.apache.spark.SparkException: An exception was raised by Python:
Traceback (most recent call last):
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/serializers.py", line 458, in dumps
    return cloudpickle.dumps(obj, pickle_protocol)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 73, in dumps
    cp.dump(obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/rdd.py", line 356, in __getnewargs__
    raise RuntimeError(
RuntimeError: It appears that you are attempting to broadcast an RDD or reference an RDD from an action or transformation. RDD transformations and actions can only be invoked by the driver, not inside of other transformatio

Traceback (most recent call last):
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/serializers.py", line 458, in dumps
    return cloudpickle.dumps(obj, pickle_protocol)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 73, in dumps
    cp.dump(obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/rdd.py", line 356, in __getnewargs__
    raise RuntimeError(
RuntimeError: It appears that you are attempting to broadcast an RDD or reference an RDD from an action or transformation. RDD transformations and actions can only be invoked by the driver, not inside of other transformations; for example, rdd1.map(lambda x: rdd2.values.count() * x) is invalid because the values transformation and count action cannot be performed inside of t

23/05/18 21:41:24 ERROR JobScheduler: Error generating jobs for time 1684417284000 ms
org.apache.spark.SparkException: An exception was raised by Python:
Traceback (most recent call last):
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/serializers.py", line 458, in dumps
    return cloudpickle.dumps(obj, pickle_protocol)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 73, in dumps
    cp.dump(obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/rdd.py", line 356, in __getnewargs__
    raise RuntimeError(
RuntimeError: It appears that you are attempting to broadcast an RDD or reference an RDD from an action or transformation. RDD transformations and actions can only be invoked by the driver, not inside of other transformatio

...

23/05/18 22:25:54 ERROR JobScheduler: Error generating jobs for time 1684419954000 ms
org.apache.spark.SparkException: An exception was raised by Python:
Traceback (most recent call last):
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/serializers.py", line 458, in dumps
    return cloudpickle.dumps(obj, pickle_protocol)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 73, in dumps
    cp.dump(obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/rdd.py", line 356, in __getnewargs__
    raise RuntimeError(
RuntimeError: It appears that you are attempting to broadcast an RDD or reference an RDD from an action or transformation. RDD transformations and actions can only be invoked by the driver, not inside of other transformatio

Traceback (most recent call last):
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/serializers.py", line 458, in dumps
    return cloudpickle.dumps(obj, pickle_protocol)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 73, in dumps
    cp.dump(obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/rdd.py", line 356, in __getnewargs__
    raise RuntimeError(
RuntimeError: It appears that you are attempting to broadcast an RDD or reference an RDD from an action or transformation. RDD transformations and actions can only be invoked by the driver, not inside of other transformations; for example, rdd1.map(lambda x: rdd2.values.count() * x) is invalid because the values transformation and count action cannot be performed inside of t

23/05/18 22:25:56 ERROR JobScheduler: Error generating jobs for time 1684419956000 ms
org.apache.spark.SparkException: An exception was raised by Python:
Traceback (most recent call last):
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/serializers.py", line 458, in dumps
    return cloudpickle.dumps(obj, pickle_protocol)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 73, in dumps
    cp.dump(obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/rdd.py", line 356, in __getnewargs__
    raise RuntimeError(
RuntimeError: It appears that you are attempting to broadcast an RDD or reference an RDD from an action or transformation. RDD transformations and actions can only be invoked by the driver, not inside of other transformatio

Traceback (most recent call last):
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/serializers.py", line 458, in dumps
    return cloudpickle.dumps(obj, pickle_protocol)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 73, in dumps
    cp.dump(obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/rdd.py", line 356, in __getnewargs__
    raise RuntimeError(
RuntimeError: It appears that you are attempting to broadcast an RDD or reference an RDD from an action or transformation. RDD transformations and actions can only be invoked by the driver, not inside of other transformations; for example, rdd1.map(lambda x: rdd2.values.count() * x) is invalid because the values transformation and count action cannot be performed inside of t

23/05/18 22:25:58 ERROR JobScheduler: Error generating jobs for time 1684419958000 ms
org.apache.spark.SparkException: An exception was raised by Python:
Traceback (most recent call last):
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/serializers.py", line 458, in dumps
    return cloudpickle.dumps(obj, pickle_protocol)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 73, in dumps
    cp.dump(obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/cloudpickle/cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "/Users/tianjiaohe/spark/spark-3.3.1-bin-hadoop2/python/pyspark/rdd.py", line 356, in __getnewargs__
    raise RuntimeError(
RuntimeError: It appears that you are attempting to broadcast an RDD or reference an RDD from an action or transformation. RDD transformations and actions can only be invoked by the driver, not inside of other transformatio